#### Group members:
Ying LI 1155151488\
Ting Yuan LIN 1155148842\
Luofeng FENG 1155151520\
Anson Au-Yeung 1155148839

In [1]:
# Pre-Processing
import string
from nltk.tokenize import RegexpTokenizer
from nltk.corpus import stopwords
import re
from nltk.stem import PorterStemmer

# Modeling
import statsmodels.api as sm
from nltk.sentiment.vader import SentimentIntensityAnalyzer
from nltk.sentiment.util import *
from nltk.util import ngrams
from collections import Counter
from gensim.models import word2vec
from nltk.tokenize import word_tokenize
from gensim import corpora, models, similarities
from nltk.stem.lancaster import LancasterStemmer
from nltk.stem.porter import PorterStemmer

# For the first-time user, you should download these two pre-trained tokenizer
#nltk.download('punkt') 
#nltk.download('stopwords')

import numpy as np
import pandas as pd

In [2]:
df = pd.read_csv('Womens Clothing E-Commerce Reviews.csv',index_col = 0)
sentiment_label = df["Recommended IND"]
df.head()

Clothing ID  Age                    Title  \
0          767   33                      NaN   
1         1080   34                      NaN   
2         1077   60  Some major design flaws   
3         1049   50         My favorite buy!   
4          847   47         Flattering shirt   

                                         Review Text  Rating  Recommended IND  \
0  Absolutely wonderful - silky and sexy and comf...       4                1   
1  Love this dress!  it's sooo pretty.  i happene...       5                1   
2  I had such high hopes for this dress and reall...       3                0   
3  I love, love, love this jumpsuit. it's fun, fl...       5                1   
4  This shirt is very flattering to all due to th...       5                1   

   Positive Feedback Count   Division Name Department Name Class Name  
0                        0       Initmates        Intimate  Intimates  
1                        4         General         Dresses    Dresses  
2                        0         General         Dresses    Dresses  
3                        0  General Petite         Bottoms      Pants  
4                        6         General            Tops    Blouses

In [3]:
# Pre-process
# choose review text
pdtextpreprocess = df[["Title","Review Text", "Rating"]]
pdtextpreprocess

Title  \
0                                                    NaN   
1                                                    NaN   
2                                Some major design flaws   
3                                       My favorite buy!   
4                                       Flattering shirt   
...                                                  ...   
23481                     Great dress for many occasions   
23482                         Wish it was made of cotton   
23483                              Cute, but see through   
23484  Very cute dress, perfect for summer parties an...   
23485                    Please make more like this one!   

                                             Review Text  Rating  
0      Absolutely wonderful - silky and sexy and comf...       4  
1      Love this dress!  it's sooo pretty.  i happene...       5  
2      I had such high hopes for this dress and reall...       3  
3      I love, love, love this jumpsuit. it's fun, fl...       5  
4      This shirt is very flattering to all due to th...       5  
...                                                  ...     ...  
23481  I was very happy to snag this dress at such a ...       5  
23482  It reminds me of maternity clothes. soft, stre...       3  
23483  This fit well, but the top was very see throug...       3  
23484  I bought this dress for a wedding i have this ...       3  
23485  This dress in a lovely platinum is feminine an...       5  

[23486 rows x 3 columns]

In [4]:
pdtextpreprocess['index'] = pdtextpreprocess.index
pdtextpreprocess


<ipython-input-4-91e5e5d2b446>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pdtextpreprocess['index'] = pdtextpreprocess.index


Title  \
0                                                    NaN   
1                                                    NaN   
2                                Some major design flaws   
3                                       My favorite buy!   
4                                       Flattering shirt   
...                                                  ...   
23481                     Great dress for many occasions   
23482                         Wish it was made of cotton   
23483                              Cute, but see through   
23484  Very cute dress, perfect for summer parties an...   
23485                    Please make more like this one!   

                                             Review Text  Rating  index  
0      Absolutely wonderful - silky and sexy and comf...       4      0  
1      Love this dress!  it's sooo pretty.  i happene...       5      1  
2      I had such high hopes for this dress and reall...       3      2  
3      I love, love, love this jumpsuit. it's fun, fl...       5      3  
4      This shirt is very flattering to all due to th...       5      4  
...                                                  ...     ...    ...  
23481  I was very happy to snag this dress at such a ...       5  23481  
23482  It reminds me of maternity clothes. soft, stre...       3  23482  
23483  This fit well, but the top was very see throug...       3  23483  
23484  I bought this dress for a wedding i have this ...       3  23484  
23485  This dress in a lovely platinum is feminine an...       5  23485  

[23486 rows x 4 columns]

In [5]:
# add title as part of review text
documents = [str(m)+" "+str(n) for m,n in zip(pdtextpreprocess["Title"],pdtextpreprocess["Review Text"])]

documents

['nan Absolutely wonderful - silky and sexy and comfortable',
 'nan Love this dress!  it\'s sooo pretty.  i happened to find it in a store, and i\'m glad i did bc i never would have ordered it online bc it\'s petite.  i bought a petite and am 5\'8".  i love the length on me- hits just a little below the knee.  would definitely be a true midi on someone who is truly petite.',
 'Some major design flaws I had such high hopes for this dress and really wanted it to work for me. i initially ordered the petite small (my usual size) but i found this to be outrageously small. so small in fact that i could not zip it up! i reordered it in petite medium, which was just ok. overall, the top half was comfortable and fit nicely, but the bottom half had a very tight under layer and several somewhat cheap (net) over layers. imo, a major design flaw was the net over layer sewn directly into the zipper - it c',
 "My favorite buy! I love, love, love this jumpsuit. it's fun, flirty, and fabulous! every ti

In [6]:
#text tokenized and transformed to lowercase
texts_tokenized = [[word.lower() for word in word_tokenize(str(document))] for document in documents]
texts_tokenized


[['nan',
  'absolutely',
  'wonderful',
  '-',
  'silky',
  'and',
  'sexy',
  'and',
  'comfortable'],
 ['nan',
  'love',
  'this',
  'dress',
  '!',
  'it',
  "'s",
  'sooo',
  'pretty',
  '.',
  'i',
  'happened',
  'to',
  'find',
  'it',
  'in',
  'a',
  'store',
  ',',
  'and',
  'i',
  "'m",
  'glad',
  'i',
  'did',
  'bc',
  'i',
  'never',
  'would',
  'have',
  'ordered',
  'it',
  'online',
  'bc',
  'it',
  "'s",
  'petite',
  '.',
  'i',
  'bought',
  'a',
  'petite',
  'and',
  'am',
  '5',
  "'",
  '8',
  "''",
  '.',
  'i',
  'love',
  'the',
  'length',
  'on',
  'me-',
  'hits',
  'just',
  'a',
  'little',
  'below',
  'the',
  'knee',
  '.',
  'would',
  'definitely',
  'be',
  'a',
  'true',
  'midi',
  'on',
  'someone',
  'who',
  'is',
  'truly',
  'petite',
  '.'],
 ['some',
  'major',
  'design',
  'flaws',
  'i',
  'had',
  'such',
  'high',
  'hopes',
  'for',
  'this',
  'dress',
  'and',
  'really',
  'wanted',
  'it',
  'to',
  'work',
  'for',
  'me',
 

In [7]:
#move stop_words
stop_words = set(stopwords.words('english'))
texts_filtered_stopwords = [[word for word in document if not word in stop_words] for document in texts_tokenized]
texts_filtered_stopwords


[['nan', 'absolutely', 'wonderful', '-', 'silky', 'sexy', 'comfortable'],
 ['nan',
  'love',
  'dress',
  '!',
  "'s",
  'sooo',
  'pretty',
  '.',
  'happened',
  'find',
  'store',
  ',',
  "'m",
  'glad',
  'bc',
  'never',
  'would',
  'ordered',
  'online',
  'bc',
  "'s",
  'petite',
  '.',
  'bought',
  'petite',
  '5',
  "'",
  '8',
  "''",
  '.',
  'love',
  'length',
  'me-',
  'hits',
  'little',
  'knee',
  '.',
  'would',
  'definitely',
  'true',
  'midi',
  'someone',
  'truly',
  'petite',
  '.'],
 ['major',
  'design',
  'flaws',
  'high',
  'hopes',
  'dress',
  'really',
  'wanted',
  'work',
  '.',
  'initially',
  'ordered',
  'petite',
  'small',
  '(',
  'usual',
  'size',
  ')',
  'found',
  'outrageously',
  'small',
  '.',
  'small',
  'fact',
  'could',
  'zip',
  '!',
  'reordered',
  'petite',
  'medium',
  ',',
  'ok.',
  'overall',
  ',',
  'top',
  'half',
  'comfortable',
  'fit',
  'nicely',
  ',',
  'bottom',
  'half',
  'tight',
  'layer',
  'several

In [8]:
# puncuations
english_punctuations = list(string.punctuation)
texts_filtered = [[word for word in document if not word in english_punctuations] for document in texts_filtered_stopwords]#move english_punctuations
texts_filtered


[['nan', 'absolutely', 'wonderful', 'silky', 'sexy', 'comfortable'],
 ['nan',
  'love',
  'dress',
  "'s",
  'sooo',
  'pretty',
  'happened',
  'find',
  'store',
  "'m",
  'glad',
  'bc',
  'never',
  'would',
  'ordered',
  'online',
  'bc',
  "'s",
  'petite',
  'bought',
  'petite',
  '5',
  '8',
  "''",
  'love',
  'length',
  'me-',
  'hits',
  'little',
  'knee',
  'would',
  'definitely',
  'true',
  'midi',
  'someone',
  'truly',
  'petite'],
 ['major',
  'design',
  'flaws',
  'high',
  'hopes',
  'dress',
  'really',
  'wanted',
  'work',
  'initially',
  'ordered',
  'petite',
  'small',
  'usual',
  'size',
  'found',
  'outrageously',
  'small',
  'small',
  'fact',
  'could',
  'zip',
  'reordered',
  'petite',
  'medium',
  'ok.',
  'overall',
  'top',
  'half',
  'comfortable',
  'fit',
  'nicely',
  'bottom',
  'half',
  'tight',
  'layer',
  'several',
  'somewhat',
  'cheap',
  'net',
  'layers',
  'imo',
  'major',
  'design',
  'flaw',
  'net',
  'layer',
  'sew

In [9]:
stemmer = PorterStemmer()
#stemmer =LancasterStemmer()
texts_stemmed = [[stemmer.stem(word) for word in docment] for docment in texts_filtered]
texts_stemmed


[['nan', 'absolut', 'wonder', 'silki', 'sexi', 'comfort'],
 ['nan',
  'love',
  'dress',
  "'s",
  'sooo',
  'pretti',
  'happen',
  'find',
  'store',
  "'m",
  'glad',
  'bc',
  'never',
  'would',
  'order',
  'onlin',
  'bc',
  "'s",
  'petit',
  'bought',
  'petit',
  '5',
  '8',
  "''",
  'love',
  'length',
  'me-',
  'hit',
  'littl',
  'knee',
  'would',
  'definit',
  'true',
  'midi',
  'someon',
  'truli',
  'petit'],
 ['major',
  'design',
  'flaw',
  'high',
  'hope',
  'dress',
  'realli',
  'want',
  'work',
  'initi',
  'order',
  'petit',
  'small',
  'usual',
  'size',
  'found',
  'outrag',
  'small',
  'small',
  'fact',
  'could',
  'zip',
  'reorder',
  'petit',
  'medium',
  'ok.',
  'overal',
  'top',
  'half',
  'comfort',
  'fit',
  'nice',
  'bottom',
  'half',
  'tight',
  'layer',
  'sever',
  'somewhat',
  'cheap',
  'net',
  'layer',
  'imo',
  'major',
  'design',
  'flaw',
  'net',
  'layer',
  'sewn',
  'directli',
  'zipper',
  'c'],
 ['favorit',
  '

In [10]:
all_stems = sum(texts_stemmed, [])
all_stems

['nan',
 'absolut',
 'wonder',
 'silki',
 'sexi',
 'comfort',
 'nan',
 'love',
 'dress',
 "'s",
 'sooo',
 'pretti',
 'happen',
 'find',
 'store',
 "'m",
 'glad',
 'bc',
 'never',
 'would',
 'order',
 'onlin',
 'bc',
 "'s",
 'petit',
 'bought',
 'petit',
 '5',
 '8',
 "''",
 'love',
 'length',
 'me-',
 'hit',
 'littl',
 'knee',
 'would',
 'definit',
 'true',
 'midi',
 'someon',
 'truli',
 'petit',
 'major',
 'design',
 'flaw',
 'high',
 'hope',
 'dress',
 'realli',
 'want',
 'work',
 'initi',
 'order',
 'petit',
 'small',
 'usual',
 'size',
 'found',
 'outrag',
 'small',
 'small',
 'fact',
 'could',
 'zip',
 'reorder',
 'petit',
 'medium',
 'ok.',
 'overal',
 'top',
 'half',
 'comfort',
 'fit',
 'nice',
 'bottom',
 'half',
 'tight',
 'layer',
 'sever',
 'somewhat',
 'cheap',
 'net',
 'layer',
 'imo',
 'major',
 'design',
 'flaw',
 'net',
 'layer',
 'sewn',
 'directli',
 'zipper',
 'c',
 'favorit',
 'buy',
 'love',
 'love',
 'love',
 'jumpsuit',
 "'s",
 'fun',
 'flirti',
 'fabul',
 'everi

In [11]:
stems_once = set(stem for stem in set(all_stems) if all_stems.count(stem) == 1)
stems_once

{'curvac',
 'patt',
 'deviat',
 'springy/summeri',
 'knox',
 'man-repel',
 'jersey-styl',
 'feel-tru',
 'anyt',
 'warm-ish',
 'slone',
 'zowi',
 'ahhhh',
 '=0',
 'syle',
 'heater',
 '117bl',
 'lovely-run',
 '26.25',
 'this.top',
 'bagg',
 'toil',
 "'stress",
 'someway',
 "'bewar",
 'funnili',
 'peephole/keyhol',
 'filigre',
 'though-th',
 "'overs",
 'vocod',
 'fitting/slend',
 'big0',
 'w/jean',
 'paid-',
 'vintage-made-modern',
 'theblack',
 'square-',
 'rail-thin',
 'feel/look',
 'bmeant',
 'silky/satini',
 'jeans-sup',
 'nansen',
 'steam/press',
 'purple/black/blu',
 'ho',
 'frump',
 'to',
 'tough-',
 'xs/sp',
 'shoulder/bodic',
 'airier',
 'cream/black',
 'befo',
 'body/width',
 'tulip-lik',
 'freshman',
 'monogram/hwr',
 'cute-as-all-get-out',
 'comfy=win',
 'unhealthili',
 'anorex',
 'cavern',
 'boohoo',
 'uno',
 'are-if',
 "'more",
 'person-check',
 'swisuit',
 'skin/color',
 '..............',
 'assymetr',
 'pettt',
 'assessments-',
 'fondli',
 'marin',
 'yellow/mango',
 '115-12

In [12]:
texts = [[stem for stem in text if stem not in stems_once] for text in texts_stemmed]
texts

[['nan', 'absolut', 'wonder', 'silki', 'sexi', 'comfort'],
 ['nan',
  'love',
  'dress',
  "'s",
  'sooo',
  'pretti',
  'happen',
  'find',
  'store',
  "'m",
  'glad',
  'bc',
  'never',
  'would',
  'order',
  'onlin',
  'bc',
  "'s",
  'petit',
  'bought',
  'petit',
  '5',
  '8',
  "''",
  'love',
  'length',
  'me-',
  'hit',
  'littl',
  'knee',
  'would',
  'definit',
  'true',
  'midi',
  'someon',
  'truli',
  'petit'],
 ['major',
  'design',
  'flaw',
  'high',
  'hope',
  'dress',
  'realli',
  'want',
  'work',
  'initi',
  'order',
  'petit',
  'small',
  'usual',
  'size',
  'found',
  'outrag',
  'small',
  'small',
  'fact',
  'could',
  'zip',
  'reorder',
  'petit',
  'medium',
  'ok.',
  'overal',
  'top',
  'half',
  'comfort',
  'fit',
  'nice',
  'bottom',
  'half',
  'tight',
  'layer',
  'sever',
  'somewhat',
  'cheap',
  'net',
  'layer',
  'imo',
  'major',
  'design',
  'flaw',
  'net',
  'layer',
  'sewn',
  'directli',
  'zipper',
  'c'],
 ['favorit',
  '

In [13]:
from gensim.corpora import Dictionary

dictionary = Dictionary(texts)  # fit dictionary
corpus = [dictionary.doc2bow(line) for line in texts]  # convert corpus to BoW format
corpus

[[(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1)],
 [(2, 1),
  (6, 1),
  (7, 1),
  (8, 2),
  (9, 1),
  (10, 1),
  (11, 2),
  (12, 1),
  (13, 1),
  (14, 1),
  (15, 1),
  (16, 1),
  (17, 1),
  (18, 1),
  (19, 1),
  (20, 1),
  (21, 1),
  (22, 2),
  (23, 1),
  (24, 1),
  (25, 1),
  (26, 1),
  (27, 1),
  (28, 3),
  (29, 1),
  (30, 1),
  (31, 1),
  (32, 1),
  (33, 1),
  (34, 1),
  (35, 2)],
 [(1, 1),
  (14, 1),
  (27, 1),
  (28, 2),
  (36, 1),
  (37, 1),
  (38, 1),
  (39, 1),
  (40, 2),
  (41, 1),
  (42, 1),
  (43, 1),
  (44, 2),
  (45, 1),
  (46, 2),
  (47, 1),
  (48, 1),
  (49, 1),
  (50, 1),
  (51, 3),
  (52, 2),
  (53, 1),
  (54, 2),
  (55, 1),
  (56, 1),
  (57, 1),
  (58, 1),
  (59, 1),
  (60, 1),
  (61, 1),
  (62, 1),
  (63, 1),
  (64, 3),
  (65, 1),
  (66, 1),
  (67, 1),
  (68, 1),
  (69, 1),
  (70, 1),
  (71, 1),
  (72, 1)],
 [(8, 1),
  (22, 3),
  (73, 1),
  (74, 1),
  (75, 1),
  (76, 1),
  (77, 1),
  (78, 1),
  (79, 1),
  (80, 1),
  (81, 1),
  (82, 1),
  (83, 1),
  (84, 1),
  (85, 1

In [14]:
#calculate tf-idf
tfidf = models.TfidfModel(corpus)
#use tf-idfs to represent documents
corpus_tfidf = tfidf[corpus]


## Build the LSA and LDA topic models for the reviews. 

## LSA

In [15]:
#LSA==LSI model
from gensim.models.lsimodel import LsiModel
lsi_bow = LsiModel(corpus_tfidf,id2word=dictionary)
lsi_bow

In [16]:
for topic_id, topic in lsi_bow.print_topics(num_topics=20, num_words=10):
    print("Topic #" + str(topic_id+1))
    print(topic)
    print()

Topic #1
0.929*"nan" + 0.080*"dress" + 0.063*"top" + 0.060*"love" + 0.057*"great" + 0.055*"size" + 0.052*"fit" + 0.048*"look" + 0.047*"'s" + 0.046*"color"

Topic #2
-0.370*"nan" + 0.195*"dress" + 0.154*"top" + 0.139*"size" + 0.135*"love" + 0.131*"great" + 0.128*"fit" + 0.119*"'s" + 0.118*"look" + 0.113*"color"

Topic #3
-0.267*"dress" + 0.264*"jean" + 0.262*"great" + 0.204*"sweater" + 0.201*"shirt" + -0.194*"small" + 0.191*"comfort" + 0.180*"soft" + -0.155*"size" + 0.148*"pant"

Topic #4
0.709*"dress" + -0.267*"top" + -0.217*"shirt" + 0.138*"comfort" + 0.138*"perfect" + -0.135*"small" + -0.114*"larg" + 0.113*"beauti" + -0.111*"cute" + -0.110*"run"

Topic #5
-0.321*"pant" + 0.306*"shirt" + -0.261*"jean" + 0.209*"dress" + -0.199*"5" + 0.191*"top" + -0.168*"size" + -0.163*"''" + -0.148*"small" + -0.142*"leg"

Topic #6
0.748*"sweater" + -0.281*"shirt" + -0.247*"top" + -0.221*"cute" + 0.118*"beauti" + -0.101*"pant" + 0.101*"warm" + -0.100*"comfort" + -0.096*"great" + 0.093*"sleev"

Topic #7

In [17]:
# Separate + and -: see topic directions clearly
for n in range(20):
    print('Topic #'+str(n+1)+':')
    print('='*50)
    d1 = []
    d2 = []
    for term, wt in lsi_bow.show_topic(n, topn=20):
        if wt >= 0:
            d1.append((term, round(wt, 3)))
        else:
            d2.append((term, round(wt, 3)))

    print('Direction 1:', d1)
    print('-'*50)
    print('Direction 2:', d2)
    print('-'*50)
    print()

Topic #1:
Direction 1: [('nan', 0.929), ('dress', 0.08), ('top', 0.063), ('love', 0.06), ('great', 0.057), ('size', 0.055), ('fit', 0.052), ('look', 0.048), ("'s", 0.047), ('color', 0.046), ('cute', 0.044), ('wear', 0.044), ('beauti', 0.043), ('like', 0.042), ("n't", 0.042), ('small', 0.042), ('comfort', 0.04), ('perfect', 0.039), ("'m", 0.039), ('order', 0.038)]
--------------------------------------------------
Direction 2: []
--------------------------------------------------

Topic #2:
Direction 1: [('dress', 0.195), ('top', 0.154), ('size', 0.139), ('love', 0.135), ('great', 0.131), ('fit', 0.128), ("'s", 0.119), ('look', 0.118), ('color', 0.113), ("n't", 0.112), ('wear', 0.111), ('like', 0.108), ('small', 0.107), ('cute', 0.106), ('beauti', 0.1), ("'m", 0.1), ('perfect', 0.096), ('order', 0.096), ('would', 0.094)]
--------------------------------------------------
Direction 2: [('nan', -0.37)]
--------------------------------------------------

Topic #3:
Direction 1: [('jean', 0.

In [18]:
# matric: U, S, V^T (SVD)
import gensim
term_topic = lsi_bow.projection.u
singular_values = lsi_bow.projection.s
topic_document = (gensim.matutils.corpus2dense(lsi_bow[corpus_tfidf], len(singular_values)).T / singular_values).T
term_topic.shape, singular_values.shape, topic_document.shape

((7063, 200), (200,), (200, 23486))

In [19]:
# Topic ratio in every document. The larger the value, more dominant
document_topics = pd.DataFrame(np.round(topic_document.T, 3), 
                               columns=['T'+str(i) for i in range(1, 201)])
document_topics.head(5)

T1     T2     T3     T4     T5     T6     T7     T8     T9    T10  ...  \
0  0.007 -0.001  0.004  0.006  0.000 -0.001  0.002  0.000  0.001  0.000  ...   
1  0.005  0.006 -0.010  0.003 -0.008  0.001 -0.005 -0.007 -0.001  0.006  ...   
2  0.002  0.005 -0.007 -0.003 -0.001 -0.001  0.004  0.001 -0.000 -0.001  ...   
3  0.002  0.005  0.011  0.008 -0.001 -0.001  0.005  0.001  0.007  0.008  ...   
4  0.002  0.006  0.016 -0.005  0.011 -0.014 -0.006 -0.031  0.020  0.007  ...   

    T191   T192   T193   T194   T195   T196   T197   T198   T199   T200  
0  0.018  0.020 -0.028  0.003 -0.003  0.004 -0.000  0.012 -0.026 -0.004  
1 -0.000  0.001  0.010 -0.003  0.000 -0.005 -0.001 -0.021 -0.007 -0.017  
2 -0.001  0.001 -0.003 -0.002  0.007 -0.003  0.009  0.007 -0.007  0.003  
3 -0.004 -0.016 -0.003 -0.007  0.002  0.001 -0.020  0.004 -0.010  0.002  
4 -0.005  0.011 -0.004  0.000  0.008 -0.002 -0.012  0.005 -0.006  0.011  

[5 rows x 200 columns]

In [20]:
# from scratch
td_matrix = gensim.matutils.corpus2dense(corpus=corpus_tfidf, num_terms=len(dictionary))
print(td_matrix.shape)
td_matrix

(7063, 23486)


array([[0.36700648, 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.214822  , 0.        , 0.05345167, ..., 0.        , 0.        ,
        0.        ],
       [0.20272192, 0.07893144, 0.        , ..., 0.        , 0.        ,
        0.        ],
       ...,
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ]], dtype=float32)

In [21]:
vocabulary = np.array(list(dictionary.values()))
print('Total vocabulary size:', len(vocabulary))
vocabulary

Total vocabulary size: 7063


array(['absolut', 'comfort', 'nan', ..., 'menswar', '/white', 'crosswrap'],
      dtype='<U19')

In [22]:
# SVD
from scipy.sparse.linalg import svds
TOTAL_TOPICS = 10
u, s, vt = svds(td_matrix, k=TOTAL_TOPICS, maxiter=10000)
term_topic = u
singular_values = s
topic_document = vt
term_topic.shape, singular_values.shape, topic_document.shape

((7063, 10), (10,), (10, 23486))

In [23]:
# weight direction
tt_weights = term_topic.transpose() * singular_values[:, None]
tt_weights.shape

(10, 7063)

In [24]:
# Check 10 most influential topics
top_terms = 20
topic_key_term_idxs = np.argsort(-np.absolute(tt_weights), axis=1)[:, :top_terms]
topic_keyterm_weights = np.array([tt_weights[row, columns] 
                             for row, columns in list(zip(np.arange(TOTAL_TOPICS), topic_key_term_idxs))])
topic_keyterms = vocabulary[topic_key_term_idxs]
topic_keyterms_weights = list(zip(topic_keyterms, topic_keyterm_weights))
for n in range(TOTAL_TOPICS):
    print('Topic #'+str(n+1)+':')
    print('*'*50)
    d1 = []
    d2 = []
    terms, weights = topic_keyterms_weights[n]
    term_weights = sorted([(t, w) for t, w in zip(terms, weights)], 
                          key=lambda row: -abs(row[1]))
    for term, wt in term_weights:
        if wt >= 0:
            d1.append((term, round(wt, 3)))
        else:
            d2.append((term, round(wt, 3)))

    print('Direction 1:', d1)
    print('-'*50)
    print('Direction 2:', d2)
    print('-'*50)
    print()

Topic #1:
**************************************************
Direction 1: [('skirt', 6.754), ('cute', 2.708), ('run', 1.453), ('super', 1.181), ('waist', 1.004), ('larg', 0.871), ('realli', 0.718), ('comfi', 0.668), ('great', 0.666), ('nice', 0.629), ('big', 0.625)]
--------------------------------------------------
Direction 2: [('top', -1.177), ('perfect', -0.89), ('pant', -0.787), ('bought', -0.757), ('jean', -0.721), ('5', -0.707), ('tri', -0.639), ('store', -0.636), ('shirt', -0.625)]
--------------------------------------------------

Topic #2:
**************************************************
Direction 1: [('shirt', 3.503), ('skirt', 3.501), ('beauti', 2.382), ('blous', 1.089), ('size', 1.064), ('color', 0.98), ('gorgeou', 0.846), ('small', 0.842), ('compliment', 0.709), ('purchas', 0.688)]
--------------------------------------------------
Direction 2: [('cute', -4.302), ('super', -2.356), ('dress', -1.42), ('comfi', -1.322), ('top', -1.061), ('short', -0.992), ('sweater', -0.

In [25]:
document_topics = pd.DataFrame(np.round(topic_document.T, 3), 
                               columns=['T'+str(i) for i in range(1, TOTAL_TOPICS+1)])
document_topics

T1     T2     T3     T4     T5     T6     T7     T8     T9    T10
0     -0.000  0.001  0.001  0.002 -0.001  0.000 -0.006  0.004 -0.001  0.007
1     -0.006 -0.001 -0.007 -0.005  0.001 -0.008 -0.003 -0.010  0.006  0.005
2      0.001 -0.000  0.001  0.004 -0.001 -0.001  0.003 -0.007  0.005  0.002
3     -0.008  0.007  0.001  0.005 -0.001 -0.001 -0.008  0.011  0.005  0.002
4     -0.007  0.020 -0.031 -0.006 -0.014  0.011  0.005  0.016  0.006  0.002
...      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...
23481  0.001  0.000  0.000  0.003 -0.004  0.009 -0.020  0.004  0.006  0.002
23482  0.001 -0.004 -0.001 -0.011  0.005  0.007  0.005  0.002  0.006  0.002
23483 -0.003 -0.007  0.003 -0.003 -0.005  0.004  0.006 -0.003  0.009  0.003
23484  0.002 -0.011 -0.004  0.001 -0.005  0.003 -0.008 -0.006  0.008  0.003
23485 -0.000 -0.001  0.001  0.006 -0.003  0.002 -0.014  0.005  0.006  0.002

[23486 rows x 10 columns]

## LDA

In [26]:
#LDA model
from gensim.models.ldamodel import LdaModel
ldamodel = LdaModel(corpus=corpus, id2word=dictionary)
ldamodel

In [27]:
topics_lda=ldamodel.show_topics()
for tpc in topics_lda:
    print(tpc)

(2, '0.284*"jacket" + 0.041*"closet" + 0.024*"afraid" + 0.023*"twist" + 0.020*"waist" + 0.020*"..." + 0.017*"spring/summ" + 0.016*"love" + 0.015*"115" + 0.015*"downsid"')
(84, '0.050*"yet" + 0.044*"noth" + 0.043*"print" + 0.040*"fun" + 0.032*"seam" + 0.025*"swingi" + 0.023*"creat" + 0.023*"subtl" + 0.023*"back" + 0.018*"make"')
(56, '0.097*"great" + 0.056*"love" + 0.040*"summer" + 0.036*"comfort" + 0.034*"fit" + 0.033*"wardrob" + 0.032*"spring" + 0.026*"dress" + 0.025*"perfect" + 0.023*"wear"')
(35, '0.078*"bust" + 0.051*"area" + 0.047*"problem" + 0.041*"zipper" + 0.041*"fit" + 0.038*"jumpsuit" + 0.031*"size" + 0.021*"get" + 0.020*"torso" + 0.017*"button"')
(79, '0.111*"price" + 0.069*"sale" + 0.042*"full" + 0.033*"wrinkl" + 0.028*"worth" + 0.021*"bring" + 0.020*"year" + 0.020*"pay" + 0.020*"round" + 0.018*"color"')
(24, '0.067*"suit" + 0.035*"back" + 0.034*"strang" + 0.033*"small" + 0.031*"send" + 0.027*"top" + 0.025*"size" + 0.023*"coverag" + 0.022*"fit" + 0.020*"beauti"')
(8, '0.068

In [46]:
import pyLDAvis
import pyLDAvis.gensim
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

In [47]:
# Visualize result
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(ldamodel, corpus, dictionary)
vis

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
68    -0.053084 -0.035344       1        1  3.099363
10     0.166292 -0.083329       2        1  2.856951
58     0.078612 -0.209155       3        1  2.729501
27     0.093261  0.086308       4        1  2.549430
86     0.066765 -0.168629       5        1  2.458601
...         ...       ...     ...      ...       ...
93    -0.120868 -0.114100      96        1  0.427029
92     0.063347 -0.081447      97        1  0.411164
25     0.029003 -0.078570      98        1  0.387264
42     0.012991  0.047137      99        1  0.355527
67    -0.013789  0.052457     100        1  0.175926

[100 rows x 5 columns], topic_info=        Term          Freq         Total  Category  logprob  loglift
2        nan   3902.000000   3902.000000   Default  30.0000  30.0000
14     dress  14445.000000  14445.000000   Default  29.0000  29.0000
425  sweater   3153.000000   3153.000000   Default  28.0000  28.0000
94     shirt   3092.000000   3092.000000   Default  27.0000  27.0000
67       top   9864.000000   9864.000000   Default  26.0000  26.0000
..       ...           ...           ...       ...      ...      ...
1    comfort     12.178786   3861.423056  Topic100  -4.6684   0.5838
278     bodi     11.287371   1204.705084  Topic100  -4.7444   1.6726
167      n't     11.611088   8473.572756  Topic100  -4.7161  -0.2499
8         's     10.276931   8262.067785  Topic100  -4.8382  -0.3467
22      love      9.787167  14130.851629  Topic100  -4.8870  -0.9322

[5109 rows x 6 columns], token_table=      Topic      Freq    Term
term                         
6         1  0.006894      ''
6         2  0.007288      ''
6         3  0.327389      ''
6         4  0.005516      ''
6         5  0.097902      ''
...     ...       ...     ...
72       43  0.002390  zipper
72       64  0.004781  zipper
72       65  0.002390  zipper
72       90  0.059757  zipper
1855     82  0.850026    zoom

[23931 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[69, 11, 59, 28, 87, 83, 77, 97, 39, 57, 44, 34, 10, 46, 45, 29, 5, 75, 15, 31, 42, 40, 98, 7, 100, 36, 55, 95, 90, 1, 96, 21, 82, 88, 8, 80, 2, 27, 49, 74, 33, 64, 19, 61, 47, 89, 76, 60, 71, 54, 53, 84, 51, 25, 17, 65, 85, 48, 13, 92, 58, 38, 35, 91, 9, 78, 99, 18, 41, 52, 6, 4, 20, 81, 79, 12, 73, 23, 62, 32, 22, 16, 30, 3, 66, 50, 14, 67, 70, 63, 86, 24, 37, 72, 56, 94, 93, 26, 43, 68])

## Predict sentiment

(Recommended / Not recommended) of reviews using their bag-of-topics features by fitting a logistic regression model.

In [28]:
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.feature_extraction.text import CountVectorizer,TfidfVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import CountVectorizer



# GET FEATURES
df_lr=pdtextpreprocess.copy()
df_lr['doc']=texts
df_lr['Recommendend IND'] =sentiment_label
df_lr
training_data, testing_data = train_test_split(df_lr,random_state = 2000)
training_data=training_data.set_index('index')
testing_data=testing_data.set_index('index')

testing_data

Title  \
index                                               
7877                        Spirit of sea sprites   
12961  Warm, soft, pretty.... what's not to love?   
11949                                Darling top!   
8893                                     So small   
17670                                   Great top   
...                                           ...   
7125                   Blazer with a casual twist   
20382                                         NaN   
3964           Cute and flattering but some flaws   
20422                            Perfect cover-up   
15430                    The perfect summer dress   

                                             Review Text  Rating  \
index                                                              
7877   Very much in love with this ethereal, delicate...       5   
12961  This sweater is pretty, fits tts, feels soft a...       4   
11949  I love this top and bought my usual xs. i don'...       5   
8893   I loved this but couldn't believe how small it...       3   
17670  I liked this top so much that i purchased it i...       5   
...                                                  ...     ...   
7125   Like the style of a blazer but the fabric of d...       5   
20382  I just picked this up in store the other day! ...       5   
3964   This caught my eye and i tried it on the in th...       3   
20422  This cover-up is perfect for the beach or the ...       5   
15430  I am 5'1" and curvy, and purchased this dress ...       5   

                                                     doc  Recommendend IND  
index                                                                       
7877   [spirit, sea, much, love, ether, delic, dress,...                 1  
12961  [warm, soft, pretti, ...., 's, love, sweater, ...                 1  
11949  [darl, top, love, top, bought, usual, xs, n't,...                 1  
8893            [small, love, could, n't, believ, small]                 1  
17670  [great, top, like, top, much, purchas, two, co...                 1  
...                                                  ...               ...  
7125   [blazer, casual, twist, like, style, blazer, f...                 1  
20382  [nan, pick, store, day, absolut, love, easi, t...                 1  
3964   [cute, flatter, flaw, caught, eye, tri, store,...                 1  
20422  [perfect, cover-up, cover-up, perfect, beach, ...                 1  
15430  [perfect, summer, dress, 5, 1, '', curvi, purc...                 1  

[5872 rows x 5 columns]

In [29]:
Y_train=training_data['Recommendend IND'].values
Y_test=testing_data['Recommendend IND'].values

In [30]:
df_train=training_data[['Title','Review Text','Rating','doc']]
df_test=testing_data[['Title','Review Text','Rating','doc']]

In [31]:
# Pre-process
# choose review text
documents_train = [str(m)+" "+str(n) for m,n in zip(df_train["Title"],df_train["Review Text"])] 
documents_test = [str(m)+" "+str(n) for m,n in zip(df_test["Title"],df_test["Review Text"])] 

In [32]:
texts_tokenized_train = [[word_train.lower() for word_train in word_tokenize(str(document_train))] for document_train in documents_train]#text tokenized and transformed to lowercase
texts_tokenized_test = [[word_test.lower() for word_test in word_tokenize(str(document_test))] for document_test in documents_test]

stop_words = set(stopwords.words('english'))
texts_filtered_stopwords_train = [[word for word in document_train if not word in stop_words] for document_train in texts_tokenized_train]#move stop_words
texts_filtered_stopwords_test = [[word for word in document_test if not word in stop_words] for document_test in texts_tokenized_test]

# puncuations
english_punctuations = list(string.punctuation)
texts_filtered_train = [[word for word in document_train if not word in english_punctuations] for document_train in texts_filtered_stopwords_train]#move english_punctuations
texts_filtered_test = [[word for word in document_test if not word in english_punctuations] for document_test in texts_filtered_stopwords_test]

stemmer = PorterStemmer()
#stemmer =LancasterStemmer()
texts_stemmed_train = [[stemmer.stem(word) for word in docment_train] for docment_train in texts_filtered_train]
texts_stemmed_test = [[stemmer.stem(word) for word in docment_test] for docment_test in texts_filtered_test]

all_stems_train = sum(texts_stemmed_train, [])
all_stems_test = sum(texts_stemmed_test, [])
stems_once_train = set(stem for stem in set(all_stems_train) if all_stems_train.count(stem) == 1) #texts that appear only once
stems_once_test = set(stem for stem in set(all_stems_test) if all_stems_test.count(stem) == 1)
texts_train = [[stem for stem in text_train if stem not in stems_once_train] for text_train in texts_stemmed_train] #texts that appear more than once
texts_test = [[stem for stem in text_test if stem not in stems_once_test] for text_test in texts_stemmed_test]

In [33]:
def extract_features(training_data,testing_data,type="binary"):
    if "binary" in type:
        
        # BINARY FEATURE REPRESENTATION
        cv= CountVectorizer(binary=True)
        cv.fit_transform(training_data)
        
        train_feature_set=cv.transform(training_data)
        test_feature_set=cv.transform(testing_data)
        
        return train_feature_set,test_feature_set,cv
  
    elif "counts" in type:
        
        # COUNT BASED FEATURE REPRESENTATION
        cv= CountVectorizer(binary=False)
        cv.fit_transform(training_data.values)
        
        train_feature_set=cv.transform(training_data)
        test_feature_set=cv.transform(testing_data)
        
        return train_feature_set,test_feature_set,cv
    
    else:    
        
        # TF-IDF BASED FEATURE REPRESENTATION
        tfidf_vectorizer=TfidfVectorizer(use_idf=True)
        tfidf_vectorizer.fit_transform(training_data)
        
        train_feature_set=tfidf_vectorizer.transform(training_data)
        test_feature_set=tfidf_vectorizer.transform(testing_data)
        
        return train_feature_set,test_feature_set,tfidf_vectorizer

In [34]:
X_train,X_test,feature_transformer = extract_features(documents_train,documents_test,type='feature_rep')

In [41]:
scikit_log_reg = LogisticRegression(solver='liblinear',max_iter=10)
lr_model=scikit_log_reg.fit(X_train,Y_train)

C:\ProgramData\Anaconda3\lib\site-packages\sklearn\svm\_base.py:976: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "


In [42]:
preds=lr_model.predict(X_test)

In [43]:
actual_index=df_test.index
actual_index
df_test['pred_Recommend']=preds
df_test['actual_Recommend']=sentiment_label[actual_index]

In [44]:
df_test

Title  \
index                                               
7877                        Spirit of sea sprites   
12961  Warm, soft, pretty.... what's not to love?   
11949                                Darling top!   
8893                                     So small   
17670                                   Great top   
...                                           ...   
7125                   Blazer with a casual twist   
20382                                         NaN   
3964           Cute and flattering but some flaws   
20422                            Perfect cover-up   
15430                    The perfect summer dress   

                                             Review Text  Rating  \
index                                                              
7877   Very much in love with this ethereal, delicate...       5   
12961  This sweater is pretty, fits tts, feels soft a...       4   
11949  I love this top and bought my usual xs. i don'...       5   
8893   I loved this but couldn't believe how small it...       3   
17670  I liked this top so much that i purchased it i...       5   
...                                                  ...     ...   
7125   Like the style of a blazer but the fabric of d...       5   
20382  I just picked this up in store the other day! ...       5   
3964   This caught my eye and i tried it on the in th...       3   
20422  This cover-up is perfect for the beach or the ...       5   
15430  I am 5'1" and curvy, and purchased this dress ...       5   

                                                     doc  pred_Recommend  \
index                                                                      
7877   [spirit, sea, much, love, ether, delic, dress,...               1   
12961  [warm, soft, pretti, ...., 's, love, sweater, ...               1   
11949  [darl, top, love, top, bought, usual, xs, n't,...               1   
8893            [small, love, could, n't, believ, small]               0   
17670  [great, top, like, top, much, purchas, two, co...               1   
...                                                  ...             ...   
7125   [blazer, casual, twist, like, style, blazer, f...               1   
20382  [nan, pick, store, day, absolut, love, easi, t...               1   
3964   [cute, flatter, flaw, caught, eye, tri, store,...               1   
20422  [perfect, cover-up, cover-up, perfect, beach, ...               1   
15430  [perfect, summer, dress, 5, 1, '', curvi, purc...               1   

       actual_Recommend  
index                    
7877                  1  
12961                 1  
11949                 1  
8893                  1  
17670                 1  
...                 ...  
7125                  1  
20382                 1  
3964                  1  
20422                 1  
15430                 1  

[5872 rows x 6 columns]

## Calculate the prediction error
(Defined as the percentage of incorrect predictions)

In [45]:
from sklearn.metrics import accuracy_score
y_pred=df_test['pred_Recommend']
y_actual=df_test['actual_Recommend']
prediction_error = 1-accuracy_score(y_pred,y_actual)
print(prediction_error)

0.0987738419618529


Conclusion: The result and visualization shows that data cleasing part is not sufficient. If time allows, we will put more emphasis on the pre-process part and delete those redundant and superfluous ones. If data cleansing is conducted correctly, the NLP result would be more precise to catch the content's main topic. 